<a href="https://colab.research.google.com/github/dariakrtn/AI_2022/blob/main/lab_4_optuna.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# 0. *Импорт библиотек и вспомогательные функции/классы*

In [4]:
#!pip install optuna

In [5]:
import optuna
import sklearn.ensemble
import sklearn.svm
import logging

In [6]:
import logging
import sys

import sklearn.datasets
import sklearn.linear_model
import sklearn.model_selection
import optuna

In [7]:
from optuna.visualization import plot_contour
from optuna.visualization import plot_edf
from optuna.visualization import plot_intermediate_values
from optuna.visualization import plot_optimization_history
from optuna.visualization import plot_parallel_coordinate
from optuna.visualization import plot_param_importances
from optuna.visualization import plot_slice

# 1. *Применение оптуны на функцию Матьяса*

In [8]:
def f_mat (x, y):
  return 0.26*(x*x +y*y)-0.48*x*y

def objective(trial):
  x = trial.suggest_float('x', -10, 10)
  y = trial.suggest_float('y', -10, 10)
  return f_mat (x, y)

In [9]:
optuna.logging.disable_default_handler() 
optuna.logging.disable_propagation()
study =optuna.create_study()
study.optimize(objective, n_trials=100)


In [10]:
best_params = study.best_params
found_x = best_params['x']
found_y = best_params['y']
print(f"Found x: {found_x},  Found y: {found_y}, f_mat(x,y): {f_mat(found_x, found_y)}")

Found x: 0.6288560521739477,  Found y: 0.7798566914593561, f_mat(x,y): 0.025545014206899197


# 2. *Использование datasets Iris и оптимизация параметров с помощью optuna*

In [11]:
def objective(trial):
    iris = sklearn.datasets.load_iris()  # грузим датасет
    classes = list(set(iris.target))
    train_x, valid_x, train_y, valid_y = sklearn.model_selection.train_test_split( # разюитие на тест и тренировку в данном случае 75 на 25
        iris.data, iris.target, test_size=0.25, random_state=0
    )


    max_iter = trial.suggest_int("max_iter", 50, 400)
    verbose = trial.suggest_int("verbose", 0, 100)
    clf = sklearn.linear_model.SGDClassifier(max_iter=max_iter, verbose = verbose)

    for step in range(100):
        clf.fit(train_x, train_y)

        # Report intermediate objective value.
        intermediate_value = 1.0 - clf.score(valid_x, valid_y)
        trial.report(intermediate_value, step)

        # Handle pruning based on the intermediate value.
        if trial.should_prune():
            raise optuna.TrialPruned()

    return 1.0 - clf.score(valid_x, valid_y)


In [13]:
optuna.logging.disable_default_handler() 
optuna.logging.disable_propagation()
optuna.logging.get_logger("optuna").addHandler(logging.StreamHandler(sys.stdout))
study = optuna.create_study(pruner=optuna.pruners.MedianPruner())
study.optimize(objective, n_trials=20)

A new study created in memory with name: no-name-62128089-b334-4c80-b6b7-56ad54b38d51
A new study created in memory with name: no-name-62128089-b334-4c80-b6b7-56ad54b38d51
-- Epoch 1
Norm: 117.97, NNZs: 4, Bias: 9.824311, T: 112, Avg. loss: 13.208814
Total training time: 0.01 seconds.
-- Epoch 2
Norm: 107.17, NNZs: 4, Bias: 9.824311, T: 224, Avg. loss: 0.000000
Total training time: 0.01 seconds.
-- Epoch 3
Norm: 98.18, NNZs: 4, Bias: 9.824311, T: 336, Avg. loss: 0.000000
Total training time: 0.01 seconds.
-- Epoch 4
Norm: 90.58, NNZs: 4, Bias: 9.824311, T: 448, Avg. loss: 0.000000
Total training time: 0.01 seconds.
-- Epoch 5
Norm: 84.07, NNZs: 4, Bias: 9.824311, T: 560, Avg. loss: 0.000000
Total training time: 0.01 seconds.
-- Epoch 6
Norm: 78.43, NNZs: 4, Bias: 9.824311, T: 672, Avg. loss: 0.000000
Total training time: 0.01 seconds.
-- Epoch 7
Norm: 73.51, NNZs: 4, Bias: 9.824311, T: 784, Avg. loss: 0.000000
Total training time: 0.01 seconds.
Convergence after 7 epochs took 0.01 seco

[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   2 out of   2 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   3 out of   3 | elapsed:    0.1s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   3 out of   3 | elapsed:    0.1s finished
[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   2 out of   2 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   3 out of   3 | elapsed:    0.1s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   3 out of   3 | elapsed:    0.1s finished
[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   2 out of   2 | elapsed:    0

Norm: 55.44, NNZs: 4, Bias: 9.960278, T: 672, Avg. loss: 0.000000
Total training time: 0.01 seconds.
-- Epoch 7
Norm: 51.96, NNZs: 4, Bias: 9.960278, T: 784, Avg. loss: 0.000000
Total training time: 0.01 seconds.
Convergence after 7 epochs took 0.01 seconds
-- Epoch 1
Norm: 77.31, NNZs: 4, Bias: 0.008392, T: 112, Avg. loss: 148.954077
Total training time: 0.00 seconds.
-- Epoch 2
Norm: 157.00, NNZs: 4, Bias: 0.372786, T: 224, Avg. loss: 104.173494
Total training time: 0.00 seconds.
-- Epoch 3
Norm: 129.94, NNZs: 4, Bias: 31.408162, T: 336, Avg. loss: 117.163845
Total training time: 0.00 seconds.
-- Epoch 4
Norm: 155.39, NNZs: 4, Bias: 38.445004, T: 448, Avg. loss: 91.322578
Total training time: 0.00 seconds.
-- Epoch 5
Norm: 177.02, NNZs: 4, Bias: 38.112642, T: 560, Avg. loss: 79.203706
Total training time: 0.00 seconds.
-- Epoch 6
Norm: 183.04, NNZs: 4, Bias: 44.195722, T: 672, Avg. loss: 53.388489
Total training time: 0.00 seconds.
-- Epoch 7
Norm: 201.60, NNZs: 4, Bias: 44.558339, T

[Parallel(n_jobs=1)]: Done   3 out of   3 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   3 out of   3 | elapsed:    0.0s finished
[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   2 out of   2 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   3 out of   3 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   3 out of   3 | elapsed:    0.0s finished
[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:    0.1s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   2 out of   2 | elapsed:    0.2s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   3 out of   3 | elapsed:    0.2s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   3 out of   3 | elapsed:    0.2s finished
[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurr

Norm: 222.89, NNZs: 4, Bias: -59.422535, T: 560, Avg. loss: 38.111701
Total training time: 0.00 seconds.
-- Epoch 6
Norm: 231.28, NNZs: 4, Bias: -65.600062, T: 672, Avg. loss: 14.193527
Total training time: 0.00 seconds.
-- Epoch 7
Norm: 252.83, NNZs: 4, Bias: -77.046857, T: 784, Avg. loss: 20.928475
Total training time: 0.00 seconds.
-- Epoch 8
Norm: 265.39, NNZs: 4, Bias: -77.241065, T: 896, Avg. loss: 15.442392
Total training time: 0.01 seconds.
-- Epoch 9
Norm: 249.23, NNZs: 4, Bias: -82.509520, T: 1008, Avg. loss: 12.224924
Total training time: 0.02 seconds.
-- Epoch 10
Norm: 252.16, NNZs: 4, Bias: -87.348022, T: 1120, Avg. loss: 8.729464
Total training time: 0.03 seconds.
-- Epoch 11
Norm: 241.49, NNZs: 4, Bias: -87.363033, T: 1232, Avg. loss: 2.010516
Total training time: 0.04 seconds.
-- Epoch 12
Norm: 231.76, NNZs: 4, Bias: -87.368687, T: 1344, Avg. loss: 2.151860
Total training time: 0.10 seconds.
-- Epoch 13
Norm: 239.45, NNZs: 4, Bias: -87.389256, T: 1456, Avg. loss: 8.1955

...

[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:    0.1s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   2 out of   2 | elapsed:    0.1s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   3 out of   3 | elapsed:    0.1s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   3 out of   3 | elapsed:    0.1s finished
[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   2 out of   2 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   3 out of   3 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   3 out of   3 | elapsed:    0.0s finished
[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   2 out of   2 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   3 out of   3 | elapsed:    0.

-- Epoch 1
Norm: 73.07, NNZs: 4, Bias: 9.861188, T: 112, Avg. loss: 11.769740
Total training time: 0.00 seconds.
-- Epoch 2
Norm: 66.38, NNZs: 4, Bias: 9.861188, T: 224, Avg. loss: 0.000000
Total training time: 0.04 seconds.
-- Epoch 3
Norm: 60.81, NNZs: 4, Bias: 9.861188, T: 336, Avg. loss: 0.000000
Total training time: 0.04 seconds.
-- Epoch 4
Norm: 56.10, NNZs: 4, Bias: 9.861188, T: 448, Avg. loss: 0.000000
Total training time: 0.04 seconds.
-- Epoch 5
Norm: 52.07, NNZs: 4, Bias: 9.861188, T: 560, Avg. loss: 0.000000
Total training time: 0.04 seconds.
-- Epoch 6
Norm: 48.58, NNZs: 4, Bias: 9.861188, T: 672, Avg. loss: 0.000000
Total training time: 0.04 seconds.
-- Epoch 7
Norm: 45.53, NNZs: 4, Bias: 9.861188, T: 784, Avg. loss: 0.000000
Total training time: 0.04 seconds.
Convergence after 7 epochs took 0.04 seconds
-- Epoch 1
Norm: 127.91, NNZs: 4, Bias: -9.043397, T: 112, Avg. loss: 131.504613
Total training time: 0.00 seconds.
-- Epoch 2
Norm: 161.16, NNZs: 4, Bias: -0.223956, T: 

[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   2 out of   2 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   3 out of   3 | elapsed:    0.1s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   3 out of   3 | elapsed:    0.1s finished
[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   2 out of   2 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   3 out of   3 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   3 out of   3 | elapsed:    0.0s finished
[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   2 out of   2 | elapsed:    0.1s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   3 out of   3 | elapsed:    0.

Norm: 157.20, NNZs: 4, Bias: 134.682159, T: 3248, Avg. loss: 21.442724
Total training time: 0.13 seconds.
-- Epoch 30
Norm: 157.01, NNZs: 4, Bias: 134.721557, T: 3360, Avg. loss: 26.466427
Total training time: 0.13 seconds.
-- Epoch 31
Norm: 152.36, NNZs: 4, Bias: 137.037983, T: 3472, Avg. loss: 24.255766
Total training time: 0.13 seconds.
-- Epoch 32
Norm: 148.16, NNZs: 4, Bias: 139.266023, T: 3584, Avg. loss: 22.444418
Total training time: 0.13 seconds.
-- Epoch 33
Norm: 144.90, NNZs: 4, Bias: 139.289820, T: 3696, Avg. loss: 22.279582
Total training time: 0.13 seconds.
-- Epoch 34
Norm: 137.27, NNZs: 4, Bias: 143.516473, T: 3808, Avg. loss: 23.341088
Total training time: 0.13 seconds.
Convergence after 34 epochs took 0.13 seconds
-- Epoch 1
Norm: 255.59, NNZs: 4, Bias: -48.093740, T: 112, Avg. loss: 99.846190
Total training time: 0.00 seconds.
-- Epoch 2
Norm: 265.98, NNZs: 4, Bias: -56.559587, T: 224, Avg. loss: 28.064525
Total training time: 0.00 seconds.
-- Epoch 3
Norm: 284.29, N

[Parallel(n_jobs=1)]: Done   2 out of   2 | elapsed:    0.1s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   3 out of   3 | elapsed:    0.2s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   3 out of   3 | elapsed:    0.2s finished


In [14]:
plot_optimization_history(study)


In [15]:

plot_contour(study)


In [16]:
plot_parallel_coordinate(study)


In [17]:
plot_slice(study)


In [18]:
plot_param_importances(study)


In [19]:
plot_edf(study)